In [1]:
%reload_ext autoreload
%autoreload 2

from src.file_utils import download_file, decompress_gz,make_dir
import glob
from warcio.archiveiterator import ArchiveIterator
from bs4 import BeautifulSoup
from tqdm import tqdm
from src.parse_warc import extract_japanese_from_warc

import json
import gzip

In [16]:
from src.downloader import get_cc_path_list,cc_path_to_urls,download_warc_file

cc_path_list=get_cc_path_list()
cc_path_list[:3]

data/path_list/CC-MAIN-2023-50


['crawl-data/CC-MAIN-2023-50/segments/1700679099281.67/warc/CC-MAIN-20231128083443-20231128113443-00000.warc.gz',
 'crawl-data/CC-MAIN-2023-50/segments/1700679099281.67/warc/CC-MAIN-20231128083443-20231128113443-00001.warc.gz',
 'crawl-data/CC-MAIN-2023-50/segments/1700679099281.67/warc/CC-MAIN-20231128083443-20231128113443-00002.warc.gz']

In [17]:
cc_path=cc_path_list[0]
warc_path=download_warc_file(cc_path)

ファイルが正常にダウンロードされました: data/gz/crawl-data_CC-MAIN-2023-50_segments_1700679099281.67_warc_CC-MAIN-20231128083443-20231128113443-00000.warc.gz
data/gz/crawl-data_CC-MAIN-2023-50_segments_1700679099281.67_warc_CC-MAIN-20231128083443-20231128113443-00000.warc.gzが解凍され、data/warc/crawl-data_CC-MAIN-2023-50_segments_1700679099281.67_warc_CC-MAIN-20231128083443-20231128113443-00000.warcに保存されました。


In [18]:
with open(warc_path, 'rb') as stream:
    string = stream.read()
try:
    tag_records = extract_japanese_from_warc(warc_path)
except Exception as e:
    print("fail loading "+warc_path)



9297it [00:26, 304.34it/s] Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.
Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.
9359it [00:26, 332.25it/s]/home/user/miniconda3/envs/crawl/lib/python3.12/html/parser.py:171: XMLParsedAsHTMLWarning: It looks like you're parsing an XML document using an HTML parser. If this really is an HTML document (maybe it's XHTML?), you can ignore or filter this warning. If it's XML, you should know that using an XML parser will be more reliable. To parse this document as XML, make sure you have the lxml package installed, and pass the keyword argument `features="xml"` into the BeautifulSoup constructor.
  k = self.parse_starttag(i)
10215it [00:30, 400.57it/s]Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.
10896it [00:32, 472.87it/s]Some characters could not be decoded, and were replaced with REPLACEMENT CHARACTER.
13863it [00:45, 69.68it/s] Some char

In [19]:
tag_records

[{'record_id': 2391,
  'url': 'http://feathercloud.blks.jp/faq/04/01/',
  'title': 'Feathercloud [よくある質問-FAQ]',
  'timestamp': '2023-11-28T10:19:01Z',
  'text': [('Feathercloud [よくある質問-FAQ]', 'html'),
   ('トップページ', 'html'),
   ('製品マニュアル', 'html'),
   ('よくあるご質問[FAQ]', 'html'),
   ('トラブルシューティング', 'html'),
   ('すべてから検索', 'html'),
   ('製品マニュアルから検索', 'html'),
   ('よくある質問[FAQ]から検索', 'html'),
   ('トラブルシューティングから検索', 'html'),
   ('お知らせ', 'html'),
   ('障害情報', 'html'),
   ('マイサイトを編集', 'html'),
   ('サイトの統合・一部ページの移行・分割はできますか', 'html'),
   ('＜＜統合や移行について＞＞各サイトごとにサイトを構築・管理していますので、サイトAとサイトBを統合したり、各サイトの一部のページのみ移行することはできません。\xa0＜＜分割について＞＞\u3000分割を行...',
    'html'),
   ('よくある質問', 'html'),
   ('全般', 'html'),
   ('ご利用環境・編集関連', 'html'),
   ('コントロールパネル', 'html'),
   ('アプリを起動', 'html'),
   ('各種設定', 'html'),
   ('サイトシアター画面', 'html'),
   ('マイサイトを編集', 'html'),
   ('テンプレートを選ぶ・ブランクサイトから作成', 'html'),
   ('サイトをインポート', 'html'),
   ('サイトエディタ画面', 'html'),
   ('全般', 'html'),
   ('サイト設定', 'html'),
   ('プレビュー・サイトを公開', 'ht

In [7]:
path="data/jap_dump/crawl-data_CC-MAIN-2023-50_segments_1700679099281.67_warc_CC-MAIN-20231128083443-20231128113443-00000.warc_jap.gz.gz"
path="data/jap_dump/crawl-data_CC-MAIN-2023-50_segments_1700679099281.67_warc_CC-MAIN-20231128083443-20231128113443-00043.warc_jap.gz.gz"
# gzipで圧縮されたJSONファイルを読み込み
with gzip.open(path, 'rt', encoding='utf-8') as f:
    data_loaded = json.load(f)


In [8]:
from src.cleaner.PerplexityChecker import PerplexityChecker
from src.cleaner.WordIntegrator import WordIntegrator
from src.cleaner.LineChecker import remove_dup_lines,remove_multi_headers

In [9]:
integrator=WordIntegrator(
checker=PerplexityChecker("data/lm_sp/ja.arpa.bin",
                          "data/lm_sp/ja.sp.model",
                          ),
filter_path="dict/header_filter.txt",
start_filter_path="dict/start_filter.txt",
end_filter_path="dict/end_filter.txt"
)

In [10]:
for id in range(0,250):
    #print(id)
    record=data_loaded[id]

    lines=[i[0].strip() for i in record["text"]]

    lines=integrator(lines)
    #try:
    #    print(lines[-1])
    #    print(lines[0])
    #except:
    #    pass
    for l in lines:
        if len(l)<100:
            print(l)

1円パチンコサーチのフィーチャーフォンサイト
1円パチンコサーチにはフィーチャーフォン向け携帯サイトがあります。
買物中に打ちたくなった、出張からの帰り道に一息など、出先で携帯から2円パチンコ、10円スロットなどを設置店舗検索ができます。
コンテンツはPC版1パチサーチとほぼ同一コンテンツになりますので、外出中に見つけたニコスロ、ニコパチや遊パチ、遊スロなどの低資金遊戯台情報をリアルタイムで確認可能となっております。
是非、ご利用ください。
http://1pachi-search.com/mobile/
＃スマートフォンからはPCサイトと同じURLより閲覧可能です。
1円パチンコや5円スロットをホールで実践する前に、アプリやメーカー公認サイトなどでシミュレーションしてみてはいかがでしょうか。
1円パチンコであれば普段ホールで打てないような釘状態での遊戯体験や、5円スロットであればなかなかお目にかかれない設定6での実践体験が可能です！
実際にホールで遊戯した後に実践の復習として使ってみても良いかもしれません。
【スマートフォン用】北斗の拳　転生の章（端末拡大版）
ぱちんこAKB48アプリ絶賛配信中!!
ストリングス:RPMハリケーン130/57p
現行モデルでは展開されていないMIDサイズです。
2021年初めに購入。オムニで3回使用しましたが、合わず今まで保管していました。
バンパー部分に特に擦った痕もありません。
使用時に本グリップをレザーに巻き替えましたが、オリジナルに復元しています。
全体に良い状態であると思われますが、中古品でありますので、神経質な方は購入お控え下さい。
即購入、ご質問歓迎します。
その他についてはプロフィール御一読下さい。
smiさん
いつも使っている香水で、店舗で売っている所を見かけたことがないので、いつもネットで購入してます。注文から届くまで早かったので、よかったです。
quantumeconomics.esこの製品をおすすめするレビューivwさん
houseofmirrors.comこの製品をおすすめするレビューyukさん
3.92(162)
割引販売
低価格で高品質な中古iPhoneが手に入る専門サイトを厳選しました。
ポイントを押さえて、お買い得な中古iPhoneを手に入れましょう。
30,800円〜
イオシスけっこう安い。
バ

IndexError: list index out of range